In [1]:
import pandas as pd
import numpy as np
import os
import time
import collections

#import matplot.lib

import gensim
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
assert gensim.models.doc2vec.FAST_VERSION > -1 #parallelize doc2vec
from gensim.utils import simple_preprocess

In [2]:
import multiprocessing

workers = multiprocessing.cpu_count()

In [3]:
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

In [4]:
#os.chdir('Patent Claims')

os.chdir('D:\Datasets')

In [5]:
%%time
df=pd.read_csv('claim_2000_2014_cleaned.csv',usecols=['claim_no','claim_txt','ICL','ICC','litigation'])


Wall time: 1min 8s


In [6]:
df.head()

claim_no                                          claim_txt  ICL  ICC  \
0  8697278-17  battery comprising interior battery active ele...  106    2   
1   8697278-1  battery cell casing comprising first casing el...   97    2   
2  7385756-81  catadioptric projection objective imaging patt...  108   33   
3  7385756-94  catadioptric projection objective imaging patt...  116   33   
4  7385756-79  catadioptric projection objective imaging patt...  103   33   

   litigation  
0           0  
1           0  
2           0  
3           0  
4           0

In [7]:


class MyDataframeCorpus(object):
    def __init__(self, source_df, text_col, tag_col):
        self.source_df = source_df
        self.text_col = text_col
        self.tag_col = tag_col
      
    def __iter__(self):
        for i, row in self.source_df.iterrows():
            yield TaggedDocument(words=simple_preprocess(row[self.text_col]), 
                                 tags=[row[self.tag_col]])

corpus_for_doc2vec = MyDataframeCorpus(df, 'claim_txt', 'claim_no')


In [9]:
corpus_for_doc2vec = MyDataframeCorpus(df, 'claim_txt', 'claim_no')

In [10]:
model_smple = Doc2Vec(vector_size=100, # 100 should be fine based on the standards
                window=5, #change to 8
                alpha=.025, #initial learning rate
                min_alpha=0.00025, #learning rate drops linearly to this
                min_count=2, #ignores all words with total frequency lower than this.
                dm =1, #algorith 1=distributed memory , 0=distributed bag of words (PV-DBOW)
                epochs=30,
                workers=workers)#cores to use

#build the vocab on the training data
#model.build_vocab(tagged_train)

In [12]:
%%time
model_smple.build_vocab(corpus_for_doc2vec,progress_per=500000)

## Build vocab from streaming tagged document Show progress every 500k rows
## Should take ~ 30 minutes

2019-06-21 13:11:18,628 : INFO : collecting all words and their counts
2019-06-21 13:11:19,707 : INFO : PROGRESS: at example #0, processed 0 words (0/s), 0 word types, 0 tags
2019-06-21 13:13:03,411 : INFO : PROGRESS: at example #500000, processed 49597140 words (478327/s), 86304 word types, 500000 tags
2019-06-21 13:14:53,477 : INFO : PROGRESS: at example #1000000, processed 100266438 words (460355/s), 122900 word types, 1000000 tags
2019-06-21 13:16:46,452 : INFO : PROGRESS: at example #1500000, processed 151452388 words (453079/s), 151795 word types, 1500000 tags
2019-06-21 13:18:38,436 : INFO : PROGRESS: at example #2000000, processed 202518153 words (456011/s), 176503 word types, 2000000 tags
2019-06-21 13:20:30,338 : INFO : PROGRESS: at example #2500000, processed 254066538 words (460656/s), 199076 word types, 2500000 tags
2019-06-21 13:22:24,905 : INFO : PROGRESS: at example #3000000, processed 306104677 words (454222/s), 221238 word types, 3000000 tags
2019-06-21 13:24:18,901 :

Wall time: 32min 39s


In [15]:
%%time
model_smple.train(corpus_for_doc2vec, total_examples=model_smple.corpus_count, epochs=model_smple.epochs)
#train the model

2019-06-21 14:38:48,387 : INFO : training model with 16 workers on 282370 vocabulary and 100 features, using sg=0 hs=0 sample=0.001 negative=5 window=5
2019-06-21 14:38:50,466 : INFO : EPOCH 1 - PROGRESS: at 0.00% examples, 4194 words/s, in_qsize 30, out_qsize 1
2019-06-21 14:38:51,481 : INFO : EPOCH 1 - PROGRESS: at 0.04% examples, 109335 words/s, in_qsize 31, out_qsize 0
2019-06-21 14:38:52,497 : INFO : EPOCH 1 - PROGRESS: at 0.09% examples, 159522 words/s, in_qsize 31, out_qsize 0
2019-06-21 14:38:53,513 : INFO : EPOCH 1 - PROGRESS: at 0.13% examples, 192350 words/s, in_qsize 31, out_qsize 0
2019-06-21 14:38:54,528 : INFO : EPOCH 1 - PROGRESS: at 0.18% examples, 210746 words/s, in_qsize 31, out_qsize 0
2019-06-21 14:38:55,560 : INFO : EPOCH 1 - PROGRESS: at 0.23% examples, 223550 words/s, in_qsize 31, out_qsize 0
2019-06-21 14:38:56,555 : INFO : EPOCH 1 - PROGRESS: at 0.27% examples, 234884 words/s, in_qsize 31, out_qsize 0
2019-06-21 14:38:57,591 : INFO : EPOCH 1 - PROGRESS: at 0.3

Wall time: 20h 21min 50s


In [68]:
## Sample of a tagged document
next(corpus_for_doc2vec.__iter__())

TaggedDocument(words=['battery', 'comprising', 'interior', 'battery', 'active', 'elements', 'battery', 'cell', 'casing', 'said', 'cell', 'casing', 'comprising', 'first', 'casing', 'element', 'first', 'contact', 'surface', 'second', 'casing', 'element', 'second', 'contact', 'surface', 'wherein', 'assembled', 'position', 'first', 'second', 'contact', 'surfaces', 'contact', 'first', 'second', 'casing', 'elements', 'encase', 'active', 'materials', 'battery', 'cell', 'interior', 'space', 'wherein', 'least', 'one', 'gas', 'tight', 'seal', 'layer', 'arranged', 'first', 'second', 'contact', 'surfaces', 'seal', 'interior', 'space', 'characterized', 'one', 'first', 'second', 'contact', 'surfaces', 'comprises', 'electrically', 'insulating', 'void', 'volume', 'layer', 'first', 'second', 'contact', 'surfaces', 'comprises', 'formable', 'material', 'layer', 'fills', 'voids', 'surface', 'void', 'volume', 'layer', 'hermetically', 'assembled', 'position', 'form', 'seal', 'layer'], tags=['8697278-17'])

In [91]:
next(iter(corpus_for_doc2vec))

TaggedDocument(words=['battery', 'comprising', 'interior', 'battery', 'active', 'elements', 'battery', 'cell', 'casing', 'said', 'cell', 'casing', 'comprising', 'first', 'casing', 'element', 'first', 'contact', 'surface', 'second', 'casing', 'element', 'second', 'contact', 'surface', 'wherein', 'assembled', 'position', 'first', 'second', 'contact', 'surfaces', 'contact', 'first', 'second', 'casing', 'elements', 'encase', 'active', 'materials', 'battery', 'cell', 'interior', 'space', 'wherein', 'least', 'one', 'gas', 'tight', 'seal', 'layer', 'arranged', 'first', 'second', 'contact', 'surfaces', 'seal', 'interior', 'space', 'characterized', 'one', 'first', 'second', 'contact', 'surfaces', 'comprises', 'electrically', 'insulating', 'void', 'volume', 'layer', 'first', 'second', 'contact', 'surfaces', 'comprises', 'formable', 'material', 'layer', 'fills', 'voids', 'surface', 'void', 'volume', 'layer', 'hermetically', 'assembled', 'position', 'form', 'seal', 'layer'], tags=['8697278-17'])

In [21]:
model_smple.wv.vocab['vagina'].count

2098

In [79]:
model.wv.vocab['government'].count

1894

In [6]:
from gensim.test.utils import get_tmpfile

fname = get_tmpfile("Doc2vec_Patent_Claims_FINAL_dm_30e")

#model_smple.save(fname)

model = Doc2Vec.load(fname)

2019-06-24 11:53:25,259 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2019-06-24 11:53:25,259 : INFO : built Dictionary(12 unique tokens: ['computer', 'human', 'interface', 'response', 'survey']...) from 9 documents (total 29 corpus positions)
2019-06-24 11:53:25,259 : INFO : loading Doc2Vec object from C:\Users\zdwhi\AppData\Local\Temp\Doc2vec_Patent_Claims_FINAL_dm_30e
2019-06-24 11:53:37,291 : INFO : loading vocabulary recursively from C:\Users\zdwhi\AppData\Local\Temp\Doc2vec_Patent_Claims_FINAL_dm_30e.vocabulary.* with mmap=None
2019-06-24 11:53:37,291 : INFO : loading trainables recursively from C:\Users\zdwhi\AppData\Local\Temp\Doc2vec_Patent_Claims_FINAL_dm_30e.trainables.* with mmap=None
2019-06-24 11:53:37,291 : INFO : loading syn1neg from C:\Users\zdwhi\AppData\Local\Temp\Doc2vec_Patent_Claims_FINAL_dm_30e.trainables.syn1neg.npy with mmap=None
2019-06-24 11:53:37,620 : INFO : loading wv recursively from C:\Users\zdwhi\AppData\Local\Temp\Doc2vec_Patent_Claims

In [54]:
### sample output
## takes in tagged document 

def model_infer_test(df,model):
    tagged_claim = next(random_claim(df))
    inferred_vector = model.infer_vector(tagged_claim.words) # infer the vector from random claim
    sims = model.docvecs.most_similar([inferred_vector], topn=len(model.docvecs)) # this takes FOREVER with a long corpus cut the corpus in half to make it fast
    print(sims[:5])
    # Compare and print the most/median/least similar documents from the train corpus
    print('Test Document ({}): «{}»\n'.format(tagged_claim.tags, ' '.join(tagged_claim.words)))
    print(u'SIMILAR/DISSIMILAR DOCS PER MODEL %s:\n' % model)
    for label, index in [('MOST', 0),('Second', 1) ,('MEDIAN', len(sims)//2), ('LEAST', len(sims) - 1)]:
        
        print(label,index)
        #print(u'%s %s: «%s»\n' % (label, sims[index], ' '.join(df[sims[index][0]].words)))
        print(u'%s %s: «%s»\n' % (label, sims[index], df.loc[df['claim_no']==sims[index][0],['claim_txt']].values))

# This will let you get random tagged documents
def random_claim(df):
    doc_index =  np.random.randint(0,len(df))
    #row = [df.iloc[doc_index,:]['claim_txt'],df.iloc[doc_index,:]['claim_no']]
    yield TaggedDocument(words=simple_preprocess(df.iloc[doc_index,:]['claim_txt']), 
                             tags=df.iloc[doc_index,:]['claim_no'])


In [57]:
model_infer_test(df,model_smple)

[('6208475-7', 0.9243185520172119), ('6208475-3', 0.883671224117279), ('6680491-1', 0.6106572151184082), ('8913211-14', 0.5911911725997925), ('8913211-1', 0.5858227610588074)]
Test Document (6208475-7): «optical member inspection apparatus obtaining image data used inspections applying illumination light optical member one side thereof photographing optical member side comprising holder comprising frame shaped base portion plurality spaced optical member holding portions provided base portion enclose space supporting optical member formed base portion said optical member holding portions receiving face outer margin optical member mounted restriction wall restrict movement optical member mounted receiving face contacting outer margin optical member said receiving face contacting outer margin face optical member light passes operation optical member said restricting wall located said moving face»

SIMILAR/DISSIMILAR DOCS PER MODEL Doc2Vec(dm/m,d100,n5,w5,mc2,s0.001,t16):

MOST 0
MOST ('6

In [ ]:
def tag(df,index):
    yield TaggedDocument(words=simple_preprocess(row[self.text_col]), 
                             tags=[row[self.tag_col]])  

In [22]:
# This will let you get random tagged documents

def random_claim(df):
    doc_index =  np.random.randint(0,len(df))
    #row = [df.iloc[doc_index,:]['claim_txt'],df.iloc[doc_index,:]['claim_no']]
    yield TaggedDocument(words=simple_preprocess(df.iloc[doc_index,:]['claim_txt']), 
                             tags=df.iloc[doc_index,:]['claim_no']).words

In [24]:
next(random_claim(df))

['method',
 'optimizing',
 'data',
 'path',
 'along',
 'data',
 'packets',
 'exchanged',
 'first',
 'communication',
 'node',
 'second',
 'communication',
 'node',
 'communications',
 'system',
 'wherein',
 'least',
 'first',
 'communication',
 'node',
 'located',
 'foreign',
 'network',
 'method',
 'comprising',
 'steps',
 'of',
 'transmitting',
 'first',
 'communication',
 'node',
 'local',
 'connection',
 'request',
 'management',
 'entity',
 'first',
 'communication',
 'node',
 'foreign',
 'network',
 'local',
 'connection',
 'request',
 'comprising',
 'identity',
 'information',
 'second',
 'communication',
 'node',
 'determining',
 'management',
 'entity',
 'foreign',
 'network',
 'response',
 'received',
 'local',
 'connection',
 'request',
 'local',
 'data',
 'gateway',
 'foreign',
 'network',
 'based',
 'identity',
 'information',
 'second',
 'communication',
 'node',
 'wherein',
 'local',
 'data',
 'gateway',
 'determined',
 'gateway',
 'second',
 'communication',
 'node',
 '

In [58]:
%%time
#doc_index =  np.random.randint(0,len(df))
doc_index = len(df)-1
### This is faster than
row = [df.iloc[doc_index,:]['claim_txt'],df.iloc[doc_index,:]['claim_no']]
### This for some reason ?! 0 nano seconds vs 1ms 
#row = df.loc[doc_index,['claim_txt','claim_no']].values


Wall time: 0 ns


In [7]:
### attempt to vectorize the function calling along the dataframe chunks.



def get_tokens(col):
    return gensim.utils.simple_preprocess(col)

def calc_vectors(tokens,model):
    return model.infer_vector((tokens),steps=20)


In [8]:
%%time
class get_vectors(object):
    def __init__(self, source_df, text_col, tag_col,model):
        self.source_df = source_df
        self.text_col = text_col
        self.tag_col = tag_col
        self.model = model
    #### Works but does not have a way to merge with source DF  
    def __iter__(self):
        # overly verbose function give me the claim-id and the vector of the tagged document from the claim
        for i, row in self.source_df.iterrows():
            yield self.model.infer_vector(TaggedDocument(words=simple_preprocess(row[self.text_col]), 
                                 tags=[row[self.tag_col]]).words,steps=20), row[self.tag_col]
            
            
df_vect_test = get_vectors(df,'claim_txt','claim_no',model)
vecs , tags = list(map(list,zip(*df_vect_test)))
df_vectors = pd.DataFrame(data=vecs,index = tags)
df_vectors.index.name = 'claim_no'

Wall time: 6h 35min 34s


In [10]:
def text_me(i,filename,end,start):
    fake = 'done training'
    message = client.messages.create(
                                from_='whatsapp:+14155238886',
                                #body=f'Built the vocab boss it took {(end-start)/60}  minutes',
                                body=f'Your {filename} code is {fake, (end-start)/60}',
                                to='whatsapp:+19715704109'
                              )

claim_no                                          claim_txt  ICL  ICC  \
0  8697278-17  battery comprising interior battery active ele...  106    2   
1   8697278-1  battery cell casing comprising first casing el...   97    2   
2  7385756-81  catadioptric projection objective imaging patt...  108   33   
3  7385756-94  catadioptric projection objective imaging patt...  116   33   
4  7385756-79  catadioptric projection objective imaging patt...  103   33   

   litigation  
0           0  
1           0  
2           0  
3           0  
4           0

In [9]:
### Text me when this shit is done
from twilio.rest import Client

# client credentials are read from TWILIO_ACCOUNT_SID and AUTH_TOKEN
client = Client("AC50ac8d9e423ca2324fd0aaa5dc91e4d1", "76be2cf406ea4cbb4577985c95a8e4d2")

# this is the Twilio sandbox testing number
from_whatsapp_number='whatsapp:+14155238886'
# replace this number with your own WhatsApp Messaging number
to_whatsapp_number='whatsapp:+19715704109'

In [13]:
%%time
df.index=df['claim_no']
df.drop(['claim_no'],axis=1,inplace=True)
### Merge vectors with data.

df_final = pd.merge(df,df_vectors,how='inner',on='claim_no')
#df_vectors.head()

df_final.info()

<class 'pandas.core.frame.DataFrame'>
Index: 8216031 entries, 8697278-17 to 8794966-1
Columns: 104 entries, claim_txt to 99
dtypes: float64(100), int64(3), object(1)
memory usage: 6.4+ GB
Wall time: 47.3 s


In [17]:
df_final.to_csv('claims_vectors_litigation.csv',index=True)

In [ ]:
df_final.drop('claim_txt',axis=1,inplace=True)

In [18]:
del df, df_vectors, vecs , tags

In [236]:
vecs , tags = list(map(list,zip(*df_vect_test)[:10]))
blah = pd.DataFrame(data=vecs,index = tags)
blah

KeyboardInterrupt: 

In [60]:
%%time
%time tokens = df['claim_txt'].apply((lambda row : get_tokens(row)))
%time vectors = tokens.apply((lambda row : calc_vectors(row,model_smple)))
del tokens
%time df_vectors = vectors.apply(lambda x : pd.Series(x))
del vectors
#%time df_vectors.to_csv('test_vectors_to_merge.csv')

### I should use yields and generators for this but i'm in a rush

Wall time: 25min 48s


NameError: name 'model' is not defined

NameError: name 'vectors' is not defined

NameError: name 'vectors' is not defined

In [155]:
#df_vectors = df['claim_txt'][:10].apply((lambda row : get_tokens(row))).apply((lambda row : calc_vectors(row,model_smple))).apply(lambda x : pd.Series(x))

df_vect_test = get_vectors(df[:10],'claim_txt','claim_no',model_smple)

In [120]:
#df['claim_txt'][:10].apply((lambda row : get_tokens(row))).apply(lambda row :calc_vectors(row,model_smple)).apply(lambda x : pd.Series(x))

0         1         2         3         4         5         6   \
0 -0.107780  0.601903 -0.280853  1.677937  0.994736  0.235104  1.099690   
1  0.082769  0.234462 -0.274393  1.379142  1.121734 -0.188325  1.042254   
2  1.320151  0.690203 -0.067970 -1.125389 -0.337494  0.058603 -0.826842   
3  0.914507  0.658234 -0.768697 -1.065891 -0.476972 -0.237683 -0.692387   
4  1.352883  0.808135 -0.072673 -0.470193 -0.485823  0.561617 -1.215139   
5  1.408415  0.846687 -0.805871 -0.876863 -0.466241 -0.739602  0.132335   
6  1.318740  0.698713 -0.385702 -1.100168 -0.442286 -0.216008 -0.936316   
7  1.858155  0.607933 -1.038954 -0.587242 -0.360321  0.558012 -0.145877   
8  1.149071  0.312484 -0.190671 -0.931803 -0.600381  0.152480 -0.773522   
9  1.257515  0.557460 -0.620070 -1.034003 -0.266954 -0.278317 -0.825467   

         7         8         9     ...           90        91        92  \
0  0.570822 -0.049077 -0.091883    ...    -1.192746 -0.437771  0.379722   
1  0.574875  0.176861 -0.112893    ...    -1.288304 -0.174551  0.651207   
2 -0.530852 -1.930141  0.372839    ...     0.378466  0.830113  0.525041   
3 -0.876860 -1.983994  0.167530    ...     0.792587  0.467129  1.026224   
4 -0.712734 -1.916998 -0.205722    ...    -0.096859  0.771595  1.237172   
5 -0.796044 -1.833705  0.908808    ...     0.267910  0.471827  0.706786   
6 -0.799015 -1.737944  0.412731    ...     0.525124  0.721694  0.633345   
7 -0.747977 -1.872106  0.479062    ...    -0.539310  0.159923  0.916942   
8 -0.670947 -1.704858  0.126621    ...     0.324091  0.728776  0.759854   
9 -0.522083 -1.756007  0.279793    ...     0.571532  0.764547  0.822939   

         93        94        95        96        97        98        99  
0 -0.885952 -0.058186  0.336634  0.038800 -0.986657 -0.521620 -2.073683  
1 -1.192964  0.173659  0.118450  0.502758 -0.951412 -0.497529 -1.772767  
2 -1.007813 -0.331908 -0.241523 -2.430176  0.295582  0.933696  0.768533  
3 -0.892889 -0.496014 -0.411153 -2.445151  0.193088  0.689275  0.711549  
4  0.232351 -0.665515 -0.266631 -2.514383  1.209349  0.072355  0.404568  
5 -0.513137 -0.723284  0.017169 -2.018531  0.916339  0.592488  0.741021  
6 -0.538245 -0.192534 -0.212918 -2.264540  0.364803  0.543640  0.405380  
7 -0.485154 -0.149518 -0.906893 -2.459996  1.030616  0.057868  0.668389  
8 -0.864537 -0.206817 -0.561864 -2.657154  0.163633  0.713839  0.895962  
9 -0.495428 -0.351081 -0.188938 -2.575629  0.119716  0.702917  0.455640  

[10 rows x 100 columns]

In [254]:
#### Build SVD code here as vectors are already built

df_vectors.head()

0         1         2         3         4         5   \
claim_no                                                                 
8697278-17 -0.168456  0.121513 -0.442733  1.520080  1.104654  0.065989   
8697278-1   0.055070  0.314569 -0.412472  1.449835  1.040132  0.003336   
7385756-81  0.988648  0.844363 -0.095364 -1.102538 -0.502984  0.213597   
7385756-94  0.923041  0.596627 -0.413758 -0.897938 -0.250872 -0.121410   
7385756-79  1.426721  0.563008 -0.231322 -0.668665 -0.285586  0.588712   

                  6         7         8         9     ...           90  \
claim_no                                              ...                
8697278-17  1.408618  0.257577  0.217482 -0.270998    ...    -1.432265   
8697278-1   1.138571  0.589694  0.118419 -0.105024    ...    -1.122250   
7385756-81 -0.941397 -0.503736 -1.881400  0.365571    ...     0.667610   
7385756-94 -0.527496 -0.673571 -1.845000  0.153362    ...     0.557909   
7385756-79 -1.288458 -0.427384 -1.933996 -0.453841    ...    -0.173177   

                  91        92        93        94        95        96  \
claim_no                                                                 
8697278-17 -0.259948  0.438286 -1.087182  0.059236  0.301953  0.376852   
8697278-1  -0.318810  0.738439 -0.713505  0.329486  0.204217  0.484255   
7385756-81  0.886405  0.259319 -0.763766 -0.286572 -0.311936 -2.247319   
7385756-94  0.554847  1.044032 -1.064804 -0.623343 -0.301304 -2.644171   
7385756-79  0.949273  1.247701  0.168950 -0.692255 -0.219989 -2.567453   

                  97        98        99  
claim_no                                  
8697278-17 -0.914021 -0.569175 -1.864300  
8697278-1  -1.009534 -0.407251 -1.534157  
7385756-81  0.194490  0.851889  0.820564  
7385756-94  0.123964  1.081750  0.505524  
7385756-79  0.523109  0.209861  0.197399  

[5 rows x 100 columns]

In [270]:
### this is all the code you need to run TSNE on the vector out put from any doc2vec model. In my instance it takes  forever

from MulticoreTSNE import MulticoreTSNE as TSNE
import matplotlib.pyplot as plt

tsne = TSNE(
    n_iter = 20,
    n_components=3,
    perplexity=30,
    metric="euclidean",
    n_jobs=8,
    random_state=42,
    verbose=1
)

%time vectors_embeded = tsne.fit_transform(df_vectors)

In [271]:
# Insted let's parallelize Logistic regression and scikit learn with dask



In [ ]:
vectors_embeded


In [ ]:
# so we need to think about the different classification methods we will be using

## first of all our class imbalance is very large
## a naive approach will get ~99.7% accuracy

In [23]:
import dask
import dask.dataframe as dd
from sklearn.model_selection import StratifiedKFold
from dask_ml.model_selection import train_test_split

from dask.distributed import Client

client = Client()



In [24]:
client

<Client: scheduler='tcp://127.0.0.1:62416' processes=4 cores=16>

In [42]:
import dask_xgboost
import xgboost

In [47]:


### need cross fold validation and stratified split for generality but this will do
ddf_final = dd.from_pandas(df_final,npartitions=8)
y = ddf_final['litigation']
X = ddf_final.drop(['litigation'],axis=1)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.30)

del y, X

#stratified shuffle split
#from sklearn.model_selection import StratifiedShuffleSplit

#sss = StratifiedShuffleSplit(n_splits=5, test_size=0.3, random_state=0)

Dask DataFrame Structure:
                 ICL    ICC litigation        0        1        2        3        4        5        6        7        8        9       10       11       12       13       14       15       16       17       18       19       20       21       22       23       24       25       26       27       28       29       30       31       32       33       34       35       36       37       38       39       40       41       42       43       44       45       46       47       48       49       50       51       52       53       54       55       56       57       58       59       60       61       62       63       64       65       66       67       68       69       70       71       72       73       74       75       76       77       78       79       80       81       82       83       84       85       86       87       88       89       90       91       92       93       94       95       96       97       98       99
npartitions=8                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             
6009555-1      int64  int64      int64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64  float64
6360294-8        ...    ...        ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...
...              ...    ...        ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...      ...

In [48]:
params = {'objective': 'binary:logistic',
          'max_depth': 4, 'eta': 0.01, 'subsample': 0.5,
          'min_child_weight': 0.5}

bst = dask_xgboost.train(client, params, X_train, y_train, num_boost_round=10)

KeyboardInterrupt: 

In [39]:
df_final.head()

ICL  ICC  litigation         0         1         2         3  \
claim_no                                                                   
8697278-17  106    2           0 -0.021915  0.124170 -0.467477  1.725972   
8697278-1    97    2           0 -0.271349  0.260269 -0.315466  1.746054   
7385756-81  108   33           0  1.429105  0.936555 -0.296551 -1.073354   
7385756-94  116   33           0  1.027478  0.484034 -0.535233 -1.124252   
7385756-79  103   33           0  1.396978  0.419591 -0.072397 -0.642861   

                   4         5         6    ...           90        91  \
claim_no                                    ...                          
8697278-17  1.353391 -0.197958  1.234415    ...    -1.201108 -0.272672   
8697278-1   0.874254 -0.225060  0.971804    ...    -1.190130 -0.417508   
7385756-81 -0.421059 -0.114407 -0.881726    ...     0.885844  0.934247   
7385756-94 -0.382812 -0.101879 -0.348340    ...     0.772912  0.951951   
7385756-79 -0.482944  0.496666 -1.178749    ...     0.074441  1.187986   

                  92        93        94        95        96        97  \
claim_no                                                                 
8697278-17  0.649778 -1.023098  0.146432  0.122571  0.215042 -1.076661   
8697278-1   0.587534 -1.157797  0.314950  0.189521  0.474607 -1.119020   
7385756-81  0.678008 -0.752642 -0.121980 -0.623260 -2.384536  0.471751   
7385756-94  0.901475 -0.721144 -0.304449 -0.278908 -2.655865  0.323664   
7385756-79  0.909484  0.278953 -0.483475 -0.028059 -2.268470  0.986993   

                  98        99  
claim_no                        
8697278-17 -0.508896 -1.690101  
8697278-1  -0.376173 -1.699343  
7385756-81  0.874406  1.251178  
7385756-94  0.943390  0.687369  
7385756-79  0.039141  0.374451  

[5 rows x 103 columns]